<img src="https://github.com/nicholasmetherall/digital-earth-pacific-macblue-activities/blob/main/attachments/images/DE_Pacific_banner.JPG?raw=true" width="900"/>

Figure 1.1.a. Jupyter environment + Python notebooks

# Digital Earth Pacific Notebook 1 prepare postcard and load data to csv

The objective of this notebook is to prepare a geomad postcard for your AOI (masking, scaling and loading additional band ratios and spectral indices) and sampling all the datasets into a csv based on your training data geodataframe.

## Step 1.1: Configure the environment

In [66]:
from datetime import datetime
from shapely.geometry import Polygon
from shapely import box
from pyproj import CRS 
import folium
import geopandas as gpd
import numpy as np
import pandas as pd
import rasterio as rio
import xarray as xr
import rioxarray
import joblib
from ipyleaflet import basemaps
from numpy.lib.stride_tricks import sliding_window_view
import pystac_client
from dask.distributed import Client as DaskClient
from odc.stac import load, configure_s3_access
import planetary_computer
from odc.stac import load
from pystac.client import Client
from skimage.feature import graycomatrix, graycoprops
import matplotlib.pyplot as plt
from matplotlib import colors
from utils import load_data, scale, calculate_band_indices, apply_mask, mask_water, mask_urban, all_masks, do_prediction

In [67]:
# Reload scripts and imports
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [68]:
# Predefined variable for title and version

# Enter your initials
initials = "nm"

# Enter your site name
site = "tongatapu"

# Date
date = datetime.now()

# Make a clean version string
version = f"{initials}-{site}-{date.strftime('%d%m%Y')}"
print(version)

nm-tongatapu-09122025


## Step 1.2: Configure STAC access and search parameters

In [69]:
catalog = "https://stac.digitalearthpacific.org"
client = Client.open(catalog)

In [70]:
# training

In [71]:
# training.columns.unique()

In [72]:
## Use training data bounds

training = gpd.read_file(f"training-data/nm-{site}.geojson")
training = training.to_crs("EPSG:4326")
min_lon, min_lat, max_lon, max_lat = training.total_bounds

bbox = [min_lon, min_lat, max_lon, max_lat]

In [73]:
# bbox = [178.410921, -18.188382, 178.46952, -18.14731]

In [74]:
datetime = "2024"

items = client.search(
    collections=["dep_s2_geomad"],
    datetime=datetime,
    bbox=bbox
).item_collection()

print(f"Found {len(items)} items in for {datetime}")

Found 1 items in for 2024


In [75]:
measurements = ["nir", "red", "blue", "green", "emad", "smad", "bcmad", "green", "nir08", "nir09", "swir16", "swir22", "coastal", "rededge1", "rededge2", "rededge3"]
data = load_data(
    items,
    measurements,
    bbox,
)
    
# Now you can use the 'data' variable
print(data)

<xarray.Dataset> Size: 359MB
Dimensions:      (y: 2654, x: 3753, time: 1)
Coordinates:
  * y            (y) float64 21kB -2.383e+06 -2.383e+06 ... -2.41e+06 -2.41e+06
  * x            (x) float64 30kB 3.856e+06 3.856e+06 ... 3.893e+06 3.893e+06
    spatial_ref  int32 4B 3832
  * time         (time) datetime64[ns] 8B 2024-01-01
Data variables: (12/15)
    nir          (time, y, x) uint16 20MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    red          (time, y, x) uint16 20MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    blue         (time, y, x) uint16 20MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    green        (time, y, x) uint16 20MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    emad         (time, y, x) float32 40MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    smad         (time, y, x) float32 40MB dask.array<chunksize=(1, 2048, 2048), meta=np.ndarray>
    ...           ...
    swir16       (time, y, x) uint16 20MB

In [76]:
# dask_client = DaskClient(n_workers=1, threads_per_worker=16, memory_limit='16GB')
# configure_s3_access(cloud_defaults=True, requester_pays=True)

In [77]:
scaled = scale(data)
scaled = scaled.compute().squeeze()

In [78]:
scaled = calculate_band_indices(scaled)
# Dataset = scaled
# Dataset.odc.explore(vmin = 0, vmax = 0.3, bands = ["red", "green", "blue"], crs="EPSG:3832", name=site)

In [79]:
# All masks
masked_scaled, mask = all_masks(scaled, return_mask = True)
masked_scaled.odc.explore(vmin=0, vmax=0.3, bands=["red", "green", "blue"], crs="EPSG:3832", name=site)

/srv/conda/envs/notebook/lib/python3.11/site-packages/odc/geo/_rgba.py:55: RuntimeWarning: invalid value encountered in cast
  return x.astype("uint8")


In [80]:
masked_scaled

<xarray.Dataset> Size: 2GB
Dimensions:      (y: 2654, x: 3753)
Coordinates:
  * y            (y) float64 21kB -2.383e+06 -2.383e+06 ... -2.41e+06 -2.41e+06
  * x            (x) float64 30kB 3.856e+06 3.856e+06 ... 3.893e+06 3.893e+06
    spatial_ref  int32 4B 3832
    time         datetime64[ns] 8B 2024-01-01
Data variables: (12/25)
    nir          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    red          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    blue         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    green        (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    emad         (y, x) float32 40MB nan nan nan nan nan ... nan nan nan nan nan
    smad         (y, x) float32 40MB nan nan nan nan nan ... nan nan nan nan nan
    ...           ...
    evi          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    savi         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    ndwi         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    mci          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    ndci         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    nbi          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan

In [81]:
# combined_ds = masked_scaled.drop_vars("count")
combined_da = masked_scaled.to_dataarray()
combined_da = combined_da.squeeze()#.stack(dims=["y", "x"])#.transpose()
stacked_arrays_2d = combined_da.stack(new_dim=("y", "x")) 
reordered_data_array = stacked_arrays_2d.transpose('new_dim', 'variable')
stacked_arrays_2d.shape

(25, 9960462)

In [82]:
# Replace any infinities with NaN
stacked_arrays_2d = stacked_arrays_2d.where(stacked_arrays_2d != float("inf"))
stacked_arrays_2d = stacked_arrays_2d.where(stacked_arrays_2d != float("-inf"))

# Replace any NaN values with 0
df = stacked_arrays_2d.squeeze().fillna(0).transpose().to_pandas()

# Remove the all-zero rows
zero_mask = (df == 0).all(axis=1)  # Creates a boolean Series
non_zero_df = df.loc[~zero_mask]  # Filters out all-zero rows

# Create a new array to hold the predictions
full_pred = pd.Series(np.nan, index=df.index)

reordered_data_array = stacked_arrays_2d.transpose('new_dim', 'variable')

### Model training

In [83]:
reordered_data_array

<xarray.DataArray (new_dim: 9960462, variable: 25)> Size: 2GB
array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]])
Coordinates:
    spatial_ref  int32 4B 3832
    time         datetime64[ns] 8B 2024-01-01
  * variable     (variable) object 200B 'nir' 'red' 'blue' ... 'ndci' 'nbi'
  * new_dim      (new_dim) object 80MB MultiIndex
  * y            (new_dim) float64 80MB -2.383e+06 -2.383e+06 ... -2.41e+06
  * x            (new_dim) float64 80MB 3.856e+06 3.856e+06 ... 3.893e+06

In [84]:
masked_scaled

<xarray.Dataset> Size: 2GB
Dimensions:      (y: 2654, x: 3753)
Coordinates:
  * y            (y) float64 21kB -2.383e+06 -2.383e+06 ... -2.41e+06 -2.41e+06
  * x            (x) float64 30kB 3.856e+06 3.856e+06 ... 3.893e+06 3.893e+06
    spatial_ref  int32 4B 3832
    time         datetime64[ns] 8B 2024-01-01
Data variables: (12/25)
    nir          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    red          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    blue         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    green        (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    emad         (y, x) float32 40MB nan nan nan nan nan ... nan nan nan nan nan
    smad         (y, x) float32 40MB nan nan nan nan nan ... nan nan nan nan nan
    ...           ...
    evi          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    savi         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    ndwi         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    mci          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    ndci         (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan
    nbi          (y, x) float64 80MB nan nan nan nan nan ... nan nan nan nan nan

In [85]:
model = joblib.load("models/nm-tongatapu-09122025-test.model")

In [86]:
# Predict the classes
predicted = model.predict(reordered_data_array)

In [87]:
# Reshape back to the original 2D array
reordered_data_array = predicted.reshape(len(masked_scaled.y), len(masked_scaled.x))

# Convert to an xarray again, because it's easier to work with
predicted_da = xr.DataArray(
    reordered_data_array, coords={"y": masked_scaled.y, "x": masked_scaled.x}, dims=["y", "x"]
)

In [88]:
print(predicted_da.dtype)  # Check the dtype of your DataArray
predicted_da = predicted_da.astype('float32')  # Convert to float32

# Check for NaN values
if np.isnan(predicted_da).any():
    print("NaN values found in the data")
    # Handle NaN values, e.g. by filling them
    predicted_da = predicted_da.fillna(0)  # Replace NaN with 0 or appropriate value

float32


In [89]:
masked_scaled = masked_scaled.compute()

In [ ]:
# masked_scaled = masked_scaled.drop_vars("count")

predicted = do_prediction(masked_scaled, model)
predicted
# predicted.odc.explore(cmap=c_map, tiles=basemaps.Esri.WorldImagery)

In [ ]:
print(predicted)

In [ ]:
predicted = predicted.where(mask)
# `prediction` is your predicted class array# `mask` is your boolean mask, where True means masked
nodata_value = 0  # or -9999, or whatever you chooseprediction_with_mask = prediction.copy()
predicted['mask'] = nodata_value

In [ ]:
predicted.plot()

In [ ]:
# predicted.odc.write_cog("prediction_serua_3b.tif")

In [ ]:
from matplotlib import colors

classes = [ 
    [1, 'Forest_land', '#064a00'],
    [2, 'Cropland', '#b67e00' ],
    [3, 'Grassland', '#d7ffa0'],
    [4, 'Wetland', '#73ffd2'],
    [5, 'Settlements', '#bd0007'],
    [6, 'Bare_land','#919191'],
    [7, 'Surface_water','#71a8ff'],
    [8, 'Shallow_ocean','#4a8ffc'],
    [9, 'Seagrass','#fc4aea'],
    [10, 'Coral_reef', '#8f0e82'],
    [11, 'Deep_ocean','#00299f'],
    [12, 'Shrubs', '#759f00'],
]


In [ ]:
values_list = [c[0] for c in classes]
color_list = [c[2] for c in classes]

# Build a listed colormap.
c_map = colors.ListedColormap(color_list)
bounds = values_list + [14]
norm = colors.BoundaryNorm(bounds, c_map.N)

predicted.plot.imshow(cmap=c_map, norm=norm, size=10)

In [ ]:
predicted.odc.explore(cmap = c_map)

# scaled.odc.explore(vmin=0, vmax=0.3, bands=["red", "green", "blue"], crs="EPSG:3832", name=site)

In [ ]:
predicted.odc.write_cog(f"{version}-prediction.tiff")

In [ ]:
# # Create predictions from the cv model to see how well they did.
# cv_predictions = cross_val_predict(model, X, y, cv=10)

# # Assess accuracy of the predictions versus label data. I do the lookup so the rows and columns have reasonable names
# y_class = spc_lookup.loc[y.astype('int')].LULC_class.values
# pred_y_class = spc_lookup.loc[cv_predictions.astype('int')].LULC_class.values
# pd.crosstab(y_class, pred_y_class)